In [1]:
# Backprop on the Seeds Dataset
from random import seed
from random import randrange
from random import random
from csv import reader
from math import exp

# Load a CSV file
def load_csv(filename):
	dataset = list()
	with open(filename, 'r') as file:
		csv_reader = reader(file)
		for row in csv_reader:
			if not row:
				continue
			dataset.append(row)
	return dataset

# Convert string column to float
def str_column_to_float(dataset, column):
	for row in dataset:
		row[column] = float(row[column].strip())

# Convert string column to integer
def str_column_to_int(dataset, column):
	class_values = [row[column] for row in dataset]
	unique = set(class_values)
	lookup = dict()
	for i, value in enumerate(unique):
		lookup[value] = i
	for row in dataset:
		row[column] = lookup[row[column]]
	return lookup

# Find the min and max values for each column
def dataset_minmax(dataset):
	minmax = list()
	stats = [[min(column), max(column)] for column in zip(*dataset)]
	return stats

# Rescale dataset columns to the range 0-1
def normalize_dataset(dataset, minmax):
	for row in dataset:
		for i in range(len(row)-1):
			row[i] = (row[i] - minmax[i][0]) / (minmax[i][1] - minmax[i][0])

# Split a dataset into k folds
def cross_validation_split(dataset, n_folds):
	dataset_split = list()
	dataset_copy = list(dataset)
	fold_size = int(len(dataset) / n_folds)
	for i in range(n_folds):
		fold = list()
		while len(fold) < fold_size:
			index = randrange(len(dataset_copy))
			fold.append(dataset_copy.pop(index))
		dataset_split.append(fold)
	return dataset_split

# Calculate accuracy percentage
def accuracy_metric(actual, predicted):
	correct = 0
	for i in range(len(actual)):
		if actual[i] == predicted[i]:
			correct += 1
	return correct / float(len(actual)) * 100.0

# Evaluate an algorithm using a cross validation split
def evaluate_algorithm(dataset, algorithm, n_folds, *args):
	folds = cross_validation_split(dataset, n_folds)
	scores = list()
	for fold in folds:
		train_set = list(folds)
		train_set.remove(fold)
		train_set = sum(train_set, [])
		test_set = list()
		for row in fold:
			row_copy = list(row)
			test_set.append(row_copy)
			row_copy[-1] = None
		predicted = algorithm(train_set, test_set, *args)
		actual = [row[-1] for row in fold]
		accuracy = accuracy_metric(actual, predicted)
		scores.append(accuracy)
	return scores

# Calculate neuron activation for an input
def activate(weights, inputs):
	activation = weights[-1]
	for i in range(len(weights)-1):
		activation += weights[i] * inputs[i]
	return activation

# Transfer neuron activation
def transfer(activation):
	return 1.0 / (1.0 + exp(-activation))

# Forward propagate input to a network output
def forward_propagate(network, row):
	inputs = row
	for layer in network:
		new_inputs = []
		for neuron in layer:
			activation = activate(neuron['weights'], inputs)
			neuron['output'] = transfer(activation)
			new_inputs.append(neuron['output'])
		inputs = new_inputs
	return inputs

# Calculate the derivative of an neuron output
def transfer_derivative(output):
	return output * (1.0 - output)

# Backpropagate error and store in neurons
def backward_propagate_error(network, expected):
	for i in reversed(range(len(network))):
		layer = network[i]
		errors = list()
		if i != len(network)-1:
			for j in range(len(layer)):
				error = 0.0
				for neuron in network[i + 1]:
					error += (neuron['weights'][j] * neuron['delta'])
				errors.append(error)
		else:
			for j in range(len(layer)):
				neuron = layer[j]
				errors.append(expected[j] - neuron['output'])
		print('deltas: ', errors)
		for j in range(len(layer)):
			neuron = layer[j]
			neuron['delta'] = errors[j] * transfer_derivative(neuron['output'])

# Update network weights with error
def update_weights(network, row, l_rate):
	for i in range(len(network)):
		inputs = row[:-1]
		if i != 0:
			inputs = [neuron['output'] for neuron in network[i - 1]]
		for neuron in network[i]:
			for j in range(len(inputs)):
				neuron['weights'][j] += l_rate * neuron['delta'] * inputs[j]
			neuron['weights'][-1] += l_rate * neuron['delta']

# Train a network for a fixed number of epochs
def train_network(network, train, l_rate, n_epoch, n_outputs):
	for epoch in range(n_epoch):
		for row in train:
			outputs = forward_propagate(network, row)
			expected = [0 for i in range(n_outputs)]
			expected[row[-1]] = 1
			backward_propagate_error(network, expected)
			update_weights(network, row, l_rate)

# Initialize a network
def initialize_network(n_inputs, n_hidden, n_outputs):
	network = list()
	hidden_layer = [{'weights':[random() for i in range(n_inputs + 1)]} for i in range(n_hidden)]
	network.append(hidden_layer)
	output_layer = [{'weights':[random() for i in range(n_hidden + 1)]} for i in range(n_outputs)]
	network.append(output_layer)
	return network

# Make a prediction with a network
def predict(network, row):
	outputs = forward_propagate(network, row)
	return outputs.index(max(outputs))

# Backpropagation Algorithm With Stochastic Gradient Descent
def back_propagation(train, test, l_rate, n_epoch, n_hidden):
	n_inputs = len(train[0]) - 1
	n_outputs = len(set([row[-1] for row in train]))
	network = initialize_network(n_inputs, n_hidden, n_outputs)
	train_network(network, train, l_rate, n_epoch, n_outputs)
	predictions = list()
	for row in test:
		prediction = predict(network, row)
		predictions.append(prediction)
	return(predictions)

# Test Backprop on Seeds dataset
seed(1)
# load and prepare data
filename = 'wheat-seeds.csv'
dataset = load_csv(filename)
for i in range(len(dataset[0])-1):
	str_column_to_float(dataset, i)
# convert class column to integers
str_column_to_int(dataset, len(dataset[0])-1)
# normalize input variables
minmax = dataset_minmax(dataset)
normalize_dataset(dataset, minmax)
# evaluate algorithm
n_folds = 5
l_rate = 0.3
n_epoch = 500
n_hidden = 5
scores = evaluate_algorithm(dataset, back_propagation, n_folds, l_rate, n_epoch, n_hidden)
print('Scores: %s' % scores)
print('Mean Accuracy: %.3f%%' % (sum(scores)/float(len(scores))))

deltas:  [-0.9117948339974441, 0.06523358996592143, -0.7773603377659758]
deltas:  [-0.16581981025269157, -0.12961781986693813, -0.047920467856482546, -0.011708121623122448, -0.046040420830316245]
deltas:  [-0.9089579332230385, 0.06243711918528916, -0.7553599113754693]
deltas:  [-0.16649832453153476, -0.12858275599598432, -0.04299970288719081, -0.0066765719978979215, -0.04281673526188086]
deltas:  [0.06347963616710695, -0.9595250185727324, -0.7727908065682144]
deltas:  [-0.09729684775372617, -0.0749651511140694, -0.017522185974376183, -0.030326467382608812, -0.04009804486036757]
deltas:  [0.06682044633047246, -0.9535478834556079, -0.7269234393488956]
deltas:  [-0.09751060234613047, -0.07496812373229066, -0.013689110840150932, -0.028632086930041687, -0.0388058850522622]
deltas:  [0.06451000853712507, -0.9529673861266361, -0.680988113568942]
deltas:  [-0.0937357154366586, -0.07092611579847909, -0.0071304523110858765, -0.022596501411061114, -0.033139443230336844]
deltas:  [0.06332189845911

deltas:  [-0.3370623122839311, 0.5770178943213575, -0.25007891114332514]
deltas:  [-0.29311149008707954, -0.0485923161709699, 0.020708234608082958, 0.1165632869286562, -0.012416675544691445]
deltas:  [-0.3848258726185812, -0.38067888001400074, 0.7407739846596364]
deltas:  [0.07361706979741872, 0.017988793766899797, -0.05058967628237786, -0.08134103668660683, -0.06587594350263737]
deltas:  [0.5830205136977265, -0.2894952275682082, -0.2833052801732406]
deltas:  [0.21166290653666286, 0.022803342118088175, 0.004381797832499389, -0.060206811984626546, 0.050998795825589145]
deltas:  [0.5709414736196158, -0.3113617963379776, -0.2635730463271138]
deltas:  [0.22916323426762766, 0.031718451770294455, 0.010302860380616964, -0.058669823352756736, 0.05619435216296319]
deltas:  [-0.38748719161524475, 0.6173240888724716, -0.23909804242345964]
deltas:  [-0.32542022242403434, -0.05795204973008973, 0.01417964201130477, 0.11811214819859027, -0.02450307538935889]
deltas:  [-0.31971357674601536, 0.52372483

deltas:  [-0.41170107206681156, -0.051246504956976136, 0.030988832756227665, 0.13900675822650033, -0.03912128366786839]
deltas:  [0.41058542485440475, -0.15389098481503496, -0.3307506655579642]
deltas:  [0.23524057456343692, -0.0019798417783173754, 0.006578349637331102, -0.02102963592587557, 0.08490350528838474]
deltas:  [-0.40642889656456205, -0.31764635635961, 0.690551576880154]
deltas:  [0.018947563287685723, 0.036104708805910775, -0.04498504448625332, -0.0944970568074093, -0.08757023284742149]
deltas:  [-0.18143659068558401, 0.41813118272748806, -0.2985122055560905]
deltas:  [-0.3448221318439576, -0.045011029823801584, 0.03062522824321704, 0.12360646330418751, -0.0265989073367527]
deltas:  [0.5488666571548683, -0.25125375076189854, -0.32042275478265764]
deltas:  [0.38720269768936566, 0.008721962180267575, -0.004608706001232192, -0.06319022782087316, 0.11191400267945409]
deltas:  [-0.592306921659038, -0.16832883614244823, 0.6852655982994569]
deltas:  [-0.19488098008361193, 0.0196475

deltas:  [-0.4146121061191791, -0.047594429413351444, 0.04059300820263287, 0.15406853952787286, -0.03959623018008181]
deltas:  [-0.152533380025085, 0.34764466412639305, -0.2607289606359237]
deltas:  [-0.333594435263133, -0.03748906340511091, 0.03773287213381558, 0.13032417968314874, -0.02724960640149587]
deltas:  [-0.1494256096687052, 0.3315038767516968, -0.24920585929798963]
deltas:  [-0.31222287842493196, -0.03332418849212911, 0.03732483653190993, 0.12353052611215692, -0.02481937097433625]
deltas:  [-0.5422046740064375, -0.19942139353215188, 0.7018785364447433]
deltas:  [-0.234022482109311, 0.03537339284159274, -0.03875546590240522, -0.06369059873893801, -0.16527309783400063]
deltas:  [0.32018450026536427, -0.0995002509518421, -0.31708674267288633]
deltas:  [0.20252250685126452, -0.014165054752580498, 0.007866688884923083, -0.0015981413778905149, 0.08971714465154548]
deltas:  [-0.16439257374644245, 0.3698388227745546, -0.24391232343966165]
deltas:  [-0.3643428217174738, -0.0361675061

deltas:  [-0.39379627639615783, -0.23245749236246666, 0.703047608645329]
deltas:  [-0.12196502221576162, 0.06715385932341372, -0.04594553960257259, -0.11609535140398194, -0.18266401326975373]
deltas:  [0.27085020135115545, -0.05471681576191727, -0.29357128035758745]
deltas:  [0.17452192222692198, -0.025449843717688585, 0.005158024560203086, 0.007789148101037695, 0.0995643476536437]
deltas:  [0.4795172416493707, -0.1437638920524103, -0.27402724114393645]
deltas:  [0.46073203195465057, -0.021895975552860193, -0.028707453927564387, -0.07433514949789438, 0.17108556411472198]
deltas:  [-0.1227557921899721, 0.3408820563343028, -0.22643131246944811]
deltas:  [-0.3511747002277646, -0.03787893862164958, 0.04017106426849087, 0.14816001318951022, -0.02757059420251794]
deltas:  [-0.07557662842624689, 0.2164850998990563, -0.24403320483791713]
deltas:  [-0.17119798279005227, -0.02576563873603995, 0.03404398457255589, 0.0966379167897436, 0.008548807757609252]
deltas:  [-0.07035893995628284, 0.1895141

...

deltas:  [-0.024733903885041007, -0.011037769244740299, 0.04785090565210881]
deltas:  [0.0067635976612202935, 0.012532705596449853, -0.00289830919332442, -0.014125806746884056, -0.023285370335524885]
deltas:  [-0.0027272346643872894, 0.18096104057249673, -0.17611380127095916]
deltas:  [-0.2571931425937284, -0.23716767891633167, 0.08488187064563846, 0.3236897824598648, 0.21883527913992973]
deltas:  [0.008988991690484172, -0.0094086280412061, -0.008394430517780802]
deltas:  [0.0005833441267594713, -0.00024973715995925855, -0.00012808761983041479, -0.00013630146682590147, 0.0011835971985321822]
deltas:  [-0.004428803478829365, 0.0013241435626144549, -0.0011149990817970132]
deltas:  [-0.00010207663333598449, 8.094606367268665e-05, 2.5302640466409517e-05, 2.8975798374195123e-05, -0.00012195716809522135]
deltas:  [-0.0071780736736958735, 0.03105216777065012, -0.021179923885928358]
deltas:  [-0.007378519723595307, -0.006137675048642421, 0.0023332420901463883, 0.008469540764002931, 0.003291571

deltas:  [-0.13214063430307404, 0.7089030213476555, -0.0033375691639489224, -0.363835539942711, -1.1852775152349009]
deltas:  [-0.00026448506958961143, -0.35950866573904694, 0.2754255578991004]
deltas:  [0.6999768398430464, 0.6322852779704955, -0.22958756677800918, -0.8512153535657918, -0.4650110421316975]
deltas:  [-0.0042333583120331775, 0.015770764008567806, -0.011093655562862452]
deltas:  [-0.0019830886007936024, -0.001618760006542355, 0.0006312982950757743, 0.002267492521529885, 0.0008927840454858408]
deltas:  [-0.001882509946076047, 0.0008682681158070915, -0.0013329629826741214]
deltas:  [-2.703641414540069e-05, 6.2299313604049915e-06, 7.94468625743035e-06, 1.766866648354879e-05, -8.440254807858628e-06]
deltas:  [-0.0015211333743556498, 0.13732709506547702, -0.15350526696714462]
deltas:  [-0.17463234988600537, -0.16273672890224145, 0.058631180530318475, 0.22479728936226567, 0.17230598063754976]
deltas:  [-0.003151083199256515, 0.0647953863237074, -0.05257675312684356]
deltas:  [-

deltas:  [0.0326198605617705, 0.03191048136416978, -0.01130440977941391, -0.04556909087770382, -0.048836005839408836]
deltas:  [0.052966691205603045, -0.0033305745545830342, -0.050609967580537006]
deltas:  [0.0017856695187617767, -0.023155054088077498, 0.0006706023168322485, 0.013865404104633572, 0.03965076486080754]
deltas:  [-0.10365206919257747, -0.003459606658397331, 0.04047193518287584]
deltas:  [-0.03579660623362008, 0.05387769106972512, 0.008300682334162486, -0.004893443573187881, -0.0793968093418833]
deltas:  [-0.005128371189205152, -0.0025136521518500676, 0.006724083210565723]
deltas:  [0.00010521561964426433, 0.0003473454318289772, -4.909126448896836e-05, -0.00030788481605985746, -0.0005749741646749395]
deltas:  [-0.002149379147441378, 0.0011391294524190076, -0.0017373521976110896]
deltas:  [-4.0041983712253926e-05, 3.6303005219101855e-06, 1.188770422468407e-05, 2.935318173707753e-05, -4.9051924133482936e-06]
deltas:  [-0.014196296024738144, -0.0017285151389602555, 0.00731754

deltas:  [0.11498658866417732, -0.018950638231147527, -0.0872034041466128]
deltas:  [0.024875952935085592, -0.08492243229589548, -0.003158887283068264, 0.03559827044571537, 0.14163135490341225]
deltas:  [0.027380072916408316, -0.0046391952890630795, -0.02351194820469797]
deltas:  [0.0011100368854543028, -0.005742578110658363, -3.0145140505991367e-05, 0.0028997140410348936, 0.009783241012180791]
deltas:  [-0.0187840742396613, 0.021222300084404178, -0.006810365438063666]
deltas:  [-0.004257348015740696, -0.0006683213838267112, 0.0012291734540587939, 0.0031679160320037428, -0.0020648756701225025]
deltas:  [-0.05408734373067853, -0.07032115778197404, 0.255304820864546]
deltas:  [0.21362544090525604, 0.2395476908086136, -0.07852095331392342, -0.33336379595776394, -0.4501544147406361]
deltas:  [-0.005261569253984993, -0.04332558496248649, 0.07804980663453498]
deltas:  [0.03336322891881586, 0.03255213497974063, -0.011557082496653588, -0.04644757616201919, -0.04974586023125223]
deltas:  [0.052

KeyboardInterrupt: 